# Compare antibody escape maps for different antibodies

First, import Python modules:

In [1]:
import os
import pickle

import numpy

import pandas as pd

import polyclonal.alphabets
import polyclonal.plot

import yaml

Get parameterized variables from [papermill](https://papermill.readthedocs.io/):

In [2]:
# this cell tagged as parameters for papermill

import yaml

if os.path.isfile("config.yaml"):
    # if running in snakemake pipeline
    with open("config.yaml") as f:
        config = yaml.safe_load(f)
        
else:
    # running interactively
    os.chdir("../")
    with open("config.yaml") as f:
        config = yaml.safe_load(f)
    antibodies = ["COV2-2130", "2130-1-0114-112"]
    chart_html = "results/antibody_comparison/antibody_comparison.html"


In [3]:
muteffects_csv = config["muteffects_observed"]

with open(config["polyclonal_config"]) as f:
    polyclonal_config = yaml.safe_load(f)

Read models:

In [4]:
antibody_models = {
    antibody: pickle.load(
        open(os.path.join(config["escape_dir"], f"{antibody}.pickle"), "rb")
    )
    for antibody in antibodies
}

Create data frame to plot:

In [5]:
# this code only works if 

first_model = list(antibody_models.values())[0]

models = first_model.model_descriptors
if all(models == m.model_descriptors for m in antibody_models.values()):
    same_descriptors = True
else:
    same_descriptors = False
    
if any(len(m.epitopes) > 1 for m in antibody_models.values()):
    raise ValueError("only works for one-epitope models")

dfs = [
    model.mut_escape_df_w_model_values
    .rename(columns={f"escape_{config['escape_avg_method']}": "escape"})
    .merge(
        pd.read_csv(muteffects_csv)
        .rename(columns={"reference_site": "site", "effect": "functional effect"})
        .assign(site=lambda x: x["site"].astype(str))
        [["site", "wildtype", "mutant", "functional effect"]],
        validate="many_to_one",
        how="outer",
    )
    .assign(
        escape=lambda x: numpy.where(x["wildtype"] == x["mutant"], 0, x["escape"]),
        antibody=antibody
    )
    .query("escape.notnull()")
    for antibody, model in antibody_models.items()
]

df = pd.concat(dfs, ignore_index=True)

Make plot:

In [6]:
kwargs = polyclonal_config["overall_default"]["plot_kwargs"]

if "addtl_tooltip_stats" not in kwargs:
    kwargs["addtl_tooltip_stats"] = []
if same_descriptors:
    kwargs["addtl_tooltip_stats"] += df.columns[-len(models) - 2: -2].tolist()
else:
    kwargs["addtl_tooltip_stats"].append("escape_std")

kwargs["addtl_slider_stats_hide_not_filter"] = ["functional effect"]

kwargs["sites"] = first_model.sites
kwargs["alphabet"] = polyclonal.alphabets.biochem_order_aas(first_model.alphabet)

chart = polyclonal.plot.lineplot_and_heatmap(
    data_df=df,
    stat_col="escape",
    category_col="antibody",
    **kwargs,
)

chart

alt.VConcatChart(...)

In [9]:
os.makedirs(os.path.dirname(chart_html), exist_ok=True)
chart.save(chart_html)